# Wolf diet analysis

## Preparing the reference database

We'll use a small version of *Genbank* containing only mammal sequences shorter than 20kb.

```bash
obigrep -L 20000 -Z \
        ../course/data/Genbank/Release_264 \
        > gb264_small_mam.fasta.gz
```

On that small DB I'll run `obipcr`.

Vertebrate primers:

- forward: TTAGATACCCCACTATGC
- reverse: TAGAACAGGCTCCTCTAG

We'll allow for 4 mismatches at most on each primer.

In [2]:
obipcr --forward TTAGATACCCCACTATGC \
       --reverse TAGAACAGGCTCCTCTAG \
       -L 200 -e 4 -Z \
       --no-progressbar \
       ../course/data/Genbank/Release_264/small.fasta.gz \
       > vert01_raw_db.fasta.gz

INFO[0000] Number of workers set 32                     
INFO[0000] Found 1 files to process                     
INFO[0000] ../course/data/Genbank/Release_264/small.fasta.gz mime type: text/fasta 
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     


In [3]:
obiuniq -m taxid -Z \
        vert01_raw_db.fasta.gz \
        > vert01_uniq_db.fasta.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] vert01_raw_db.fasta.gz mime type: text/fasta 
INFO[0000] Running dereplication on disk with 100 chunks 
INFO[0000] Keep sigletons in the output                 
INFO[0000] Starting data splitting                      
                                                - Reading sequences (20678/-, 72999 it/s) [0s] - Splitting data set (22774/-, 78503 it/s) [0s] 

INFO[0000] Data splitted over 100 batches               
INFO[0000] End of the data splitting                    
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     
INFO[0000] /tmp/obiseq_chunks_488015107/chunk_0.fastx mime type: text/fasta 
INFO[0000] Start processing of batch 0/100 : 108 sequences 
INFO[0000] /tmp/obiseq_chunks_488015107/chunk_1.fastx mime type: text/fasta 
INFO[0000] St

In [4]:
obiannotate --add-lca-in taxid \
            -t ../course/data/ncbitaxo_20251118.tgz \
            vert01_uniq_db.fasta.gz \
  | obiannotate -t ../course/data/ncbitaxo_20251118.tgz \
            --taxonomic-rank -Z \
            > vert01_lca_db.fasta.gz

INFO[0001] NCBI Taxdump Tar Archive detected: ../course/data/ncbitaxo_20251118.tgz 
INFO[0001] Loading Taxonomy nodes                       
INFO[0001] NCBI Taxdump Tar Archive detected: ../course/data/ncbitaxo_20251118.tgz 
INFO[0001] Loading Taxonomy nodes                       
INFO[0016] 2706727 Taxonomy nodes read                  
INFO[0016] Loading Taxon names                          
INFO[0016] 2706727 Taxonomy nodes read                  
INFO[0016] Loading Taxon names                          
INFO[0038] 2706727 taxon names read                     
INFO[0038] Loading Merged taxa                          
INFO[0038] 2706727 taxon names read                     
INFO[0038] Loading Merged taxa                          
INFO[0038] 93509 merged taxa read                       
INFO[0038] Set as default taxonomy NCBI Taxonomy        
INFO[0038] Number of workers set 16                     
INFO[0038] Found 1 files to process                     
INFO[0038] vert01_uniq_db.fasta.gz

In [5]:
obicsv -k taxonomic_rank vert01_lca_db.fasta.gz \
  | tail -n +2 \
  | sort \
  | uniq -c

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] vert01_lca_db.fasta.gz mime type: text/fasta 


      4 clade
     52 family
    374 genus
      6 no rank
      1 order
   3180 species
      1 species group
     46 subfamily
      6 subgenus
      1 suborder
    180 subspecies
      6 tribe


In [6]:
obigrep --require-rank family \
        -t ../course/data/ncbitaxo_20251118.tgz \
        --update-taxid \
        vert01_lca_db.fasta.gz \
        > vert01_clean_db.fasta.gz

INFO[0000] NCBI Taxdump Tar Archive detected: ../course/data/ncbitaxo_20251118.tgz 
INFO[0000] Loading Taxonomy nodes                       
INFO[0007] 2706727 Taxonomy nodes read                  
INFO[0007] Loading Taxon names                          
INFO[0016] 2706727 taxon names read                     
INFO[0016] Loading Merged taxa                          
INFO[0016] 93509 merged taxa read                       
INFO[0016] Set as default taxonomy NCBI Taxonomy        
INFO[0016] Number of workers set 16                     
INFO[0016] Found 1 files to process                     
INFO[0016] vert01_lca_db.fasta.gz mime type: text/fasta 
INFO[0016] On output use JSON headers                   
INFO[0016] Output is done on stdout                     
INFO[0016] Data is writen to stdout                     



In [7]:
obicsv -k taxonomic_rank vert01_clean_db.fasta.gz \
  | tail -n +2 \
  | sort \
  | uniq -c

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] vert01_clean_db.fasta.gz mime type: text/fasta 


     52 family
    374 genus
      6 no rank
   3180 species
      1 species group
     46 subfamily
      6 subgenus
    180 subspecies
      6 tribe


In [8]:
obicsv -k taxid vert01_clean_db.fasta.gz \
  | tail -n +2 \
  | sort \
  | uniq \
  | awk -F'@' '{print $2}' \
  | sort \
  | uniq -c

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] vert01_clean_db.fasta.gz mime type: text/fasta 


     21 family
    188 genus
      3 no rank
   2021 species
      1 species group
     23 subfamily
      3 subgenus
     98 subspecies
      2 tribe


In [9]:
obiannotate --taxonomic-path \
            -t ../course/data/ncbitaxo_20251118.tgz \
            -Z \
            vert01_clean_db.fasta.gz \
            > vert01_ref_db.fasta.gz 

INFO[0000] NCBI Taxdump Tar Archive detected: ../course/data/ncbitaxo_20251118.tgz 
INFO[0000] Loading Taxonomy nodes                       
INFO[0007] 2706727 Taxonomy nodes read                  
INFO[0007] Loading Taxon names                          
INFO[0017] 2706727 taxon names read                     
INFO[0017] Loading Merged taxa                          
INFO[0017] 93509 merged taxa read                       
INFO[0017] Set as default taxonomy NCBI Taxonomy        
INFO[0017] Number of workers set 16                     
INFO[0017] Found 1 files to process                     
INFO[0017] vert01_clean_db.fasta.gz mime type: text/fasta 
INFO[0017] On output use JSON headers                   
INFO[0017] Output is done on stdout                     
INFO[0017] Data is writen to stdout                     



## Analyzing the metabarcoding data

### Step 1: Pairing the Reads

We'll use the `obipairing` *OBITools4* command.

In [10]:
obipairing -F ../course/data/Wolf_diet/wolf_F.fastq \
           -R ../course/data/Wolf_diet/wolf_R.fastq \
           -Z \
           > wolf_paired.fastq.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] ../course/data/Wolf_diet/wolf_F.fastq mime type: text/fastq 
INFO[0000] Found 1 files to process                     
INFO[0000] ../course/data/Wolf_diet/wolf_R.fastq mime type: text/fastq 
INFO[0000] Start of the sequence Pairing using 16 workers 
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     
INFO[0000] Initializing the DNA Scoring matrix          
                                                - Reading sequences (15525/-, 59229 it/s) [0s] | Reading sequences (19407/-, 43953 it/s) [0s] | Reading sequences (27170/-, 60156 it/s) [0s] / Reading sequences (23288/-, 42042 it/s) [0s] - Reading sequences (31052/-, 47481 it/s) [0s] | Reading sequences (38815/-, 47481 it/s) [0s] \ Reading sequences (31052/-, 27527 it/s) [1s] - Reading sequences (

In [11]:
obigrep -a mode=alignment wolf_paired.fastq.gz \
 | obicsv -k ali_length -k score_norm \
 > wolf_paired_scores.csv

INFO[0000] Number of workers set 16                     
INFO[0000] Number of workers set 16                     
INFO[0000] Reading sequences from stdin in guessed      
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_paired.fastq.gz mime type: text/fastq   
INFO[0000] mode alignment                               
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     
/ Reading sequences (5073/-, 50093 it/s) [0s] INFO[0000] - mime type: text/fastq                      
                                                Reading sequences (13538/-, 46268 it/s) [0s] | Reading sequences (15231/-, 37250 it/s) [0s] / Reading sequences (18616/-, 31567 it/s) [0s]                                        | Reading sequences (3344/-, 8180 it/s) [0s] \ Reading sequences (25387/-, 31567 it/s) [0s]                                        - Writing CSV (6692/-, 1112

In [12]:
obigrep  -a mode=alignment wolf_paired.fastq.gz \
  | obigrep -p 'annotations.score_norm >= 0.96 && 
                annotations.ali_length > 55 && 
                annotations.ali_length < 65' \
            -Z \
            > wolf_paired_good.fastq.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Number of workers set 16                     
INFO[0000] Reading sequences from stdin in guessed      
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_paired.fastq.gz mime type: text/fastq   
INFO[0000] mode alignment                               
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     
/ Reading sequences (3378/-, 17818 it/s) [0s] INFO[0000] - mime type: text/fastq                      
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     
                                                Reading sequences (8457/-, 28787 it/s) [0s] | Reading sequences (13538/-, 27278 it/s) [0s] - Reading sequences (15228/-, 22019 it/s) [0s] / Reading sequences (3348/-

In [13]:
obicount wolf_paired.fastq.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_paired.fastq.gz mime type: text/fastq   
                                                Reading sequences (16921/-, 47077 it/s) [0s] | Reading sequences (23692/-, 51190 it/s) [0s] / Reading sequences (32155/-, 56006 it/s) [0s] - Reading sequences (40629/-, 56006 it/s) [0s] \ Reading sequences (42321/-, 56006 it/s) [0s] 
| entities |         n |
| -------- | --------- |
| variants |    45,276 |
| reads    |    45,276 |
| symbols  | 7,386,937 |


In [14]:
obicount wolf_paired_good.fastq.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_paired_good.fastq.gz mime type: text/fastq 
                                                Reading sequences (13765/-, 54484 it/s) [0s] \ Reading sequences (26237/-, 74257 it/s) [0s] 
| entities |         n |
| -------- | --------- |
| variants |    27,955 |
| reads    |    27,955 |
| symbols  | 4,302,597 |


## Extracting the barcode

Using the `obimultiplex`command. 

In [15]:
obimultiplex -s ../course/data/Wolf_diet/wolf_data_wolf_diet_ngsfilter.csv \
             -u wolf_unassign.fastq.gz \
             -Z \
             wolf_paired_good.fastq.gz \
             > wolf_assign.fastq.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_paired_good.fastq.gz mime type: text/fastq 
INFO[0000] Reading NGSFilter file: ../course/data/Wolf_diet/wolf_data_wolf_diet_ngsfilter.csv 
INFO[0000] No BOM detected                              
INFO[0000] NGSFilter configuration mimetype: text/ngsfilter-csv 
INFO[0000] 3 parameters found                           
INFO[0000] Read 5 records                               
INFO[0000] First record: [experiment sample sample_tag forward_primer reverse_primer] 
INFO[0000] Set tag matching mode to strict              
INFO[0000] Set global allowed primer mismatches to 2    
INFO[0000] Disallows indels for primer matching         
INFO[0000] Unassigned sequences saved in file: wolf_unassign.fastq.gz 
INFO[0000] Sequence demultiplexing using 16 workers     
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                 

In [16]:
obicount wolf_unassign.fastq.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_unassign.fastq.gz mime type: text/fastq 

| entities |      n |
| -------- | ------ |
| variants |    243 |
| reads    |    243 |
| symbols  | 23,598 |


In [17]:
obicount wolf_assign.fastq.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_assign.fastq.gz mime type: text/fastq   
                                               eading sequences (4415/-, 14719 it/s) [0s] / Reading sequences (8829/-, 17607 it/s) [0s] - Reading sequences (11478/-, 17607 it/s) [0s] \ Reading sequences (14125/-, 17607 it/s) [0s] / Reading sequences (16774/-, 17607 it/s) [0s] - Reading sequences (19425/-, 19283 it/s) [1s] \ Reading sequences (23836/-, 19283 it/s) [1s] 
| entities |         n |
| -------- | --------- |
| variants |    27,712 |
| reads    |    27,712 |
| symbols  | 2,580,858 |


In [21]:
obicsv -k sample wolf_assign.fastq.gz \
  | tail -n +2 \
  | sort \
  | uniq -c

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_assign.fastq.gz mime type: text/fastq   
                                                Reading sequences (4416/-, 18923 it/s) [0s] - Writing CSV (4416/-, 18918 it/s) [0s] | Reading sequences (8831/-, 20349 it/s) [0s] | Writing CSV (8831/-, 20347 it/s) [0s] / Reading sequences (11477/-, 21376 it/s) [0s] / Writing CSV (11477/-, 21374 it/s) [0s] \ Reading sequences (14125/-, 21376 it/s) [0s] \ Writing CSV (14125/-, 21374 it/s) [0s] | Reading sequences (15008/-, 21376 it/s) [0s] | Writing CSV (15008/-, 21374 it/s) [0s] - Reading sequences (19425/-, 21376 it/s) [1s] - Writing CSV (19425/-, 21374 it/s) [1s] \ Reading sequences (20308/-, 18061 it/s) [1s] \ Writing CSV (20308/-, 18058 it/s) [1s] / Reading sequences (23836/-, 18061 it/s) [1s] / Writing CSV (23836/-, 18058 it/s) [1s] 

   6447 13a_F730603
   6066 15a_F730814
   9567 26a_F040644
   5632 29a_F260619
 

In [19]:
obiuniq -m sample -Z \
        wolf_assign.fastq.gz \
        > wolf_uniq.fasta.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_assign.fastq.gz mime type: text/fastq   
INFO[0000] Running dereplication on disk with 100 chunks 
INFO[0000] Keep sigletons in the output                 
INFO[0000] Starting data splitting                      
                                                 Reading sequences (4415/-, 16703 it/s) [0s] \ Splitting data set (4415/-, 12929 it/s) [0s] | Reading sequences (6179/-, 14028 it/s) [0s] | Splitting data set (7062/-, 15883 it/s) [0s] / Reading sequences (8829/-, 16246 it/s) [0s] - Splitting data set (8829/-, 13801 it/s) [0s] - Reading sequences (10595/-, 16246 it/s) [0s] \ Splitting data set (12361/-, 13801 it/s) [0s] \ Reading sequences (15008/-, 16246 it/s) [0s] | Splitting data set (15008/-, 13801 it/s) [0s] | Reading sequences (15893/-, 16246 it/s) [0s] - Splitting data set (18542/-, 13801 it/s) [1s] - Reading sequences (19425/-, 18704 it/s) [1s]

In [20]:
obicount wolf_uniq.fasta.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_uniq.fasta.gz mime type: text/fasta     

| entities |      n |
| -------- | ------ |
| variants |    989 |
| reads    | 27,712 |
| symbols  | 97,427 |


## Dataset cleaning

First step: looking at singleton sequences

In [22]:
obicsv -k count wolf_uniq.fasta.gz \
  | sort -n \
  | uniq -c \
  | head -n 10

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_uniq.fasta.gz mime type: text/fasta     


      1 count
    543 1
    125 2
     86 3
     66 4
     36 5
     14 6
     36 7
     19 8
     10 9


In [23]:
obigrep -c 2 -Z \
        wolf_uniq.fasta.gz \
        > wolf_nosingleton.fasta.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_uniq.fasta.gz mime type: text/fasta     
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     



In [25]:
obicount wolf_nosingleton.fasta.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_nosingleton.fasta.gz mime type: text/fasta 

| entities |      n |
| -------- | ------ |
| variants |    446 |
| reads    | 27,169 |
| symbols  | 43,760 |


Second step: Look at the sequence length distribution.

In [26]:
obiannotate --length \
            wolf_nosingleton.fasta.gz \
| obicsv -k seq_length \
| sort -n \
| uniq -c 

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_nosingleton.fasta.gz mime type: text/fasta 
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     
INFO[0000] Number of workers set 16                     
INFO[0000] Reading sequences from stdin in guessed      

INFO[0000] - mime type: text/fasta                      


      1 seq_length
      5 4
      1 5
      1 8
    179 99
    259 100
      1 106


In [27]:
obigrep -l 50 -Z \
        wolf_nosingleton.fasta.gz \
        > wolf_noshort.fasta.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_nosingleton.fasta.gz mime type: text/fasta 
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     



In [29]:
obicount wolf_noshort.fasta.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_noshort.fasta.gz mime type: text/fasta  

| entities |      n |
| -------- | ------ |
| variants |    439 |
| reads    | 25,290 |
| symbols  | 43,727 |


Step 3: Look at ambiguous nucleotides. 

In [30]:
obigrep -v -s '^[acgt]+$' \
        wolf_noshort.fasta.gz \
| obicount | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] Number of workers set 16                     
INFO[0000] Reading sequences from stdin in guessed      
INFO[0000] wolf_noshort.fasta.gz mime type: text/fasta  
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     

INFO[0000] - mime type: text/fasta                      

| entities |   n |
| -------- | --- |
| variants |   4 |
| reads    |  10 |
| symbols  | 399 |


In [31]:
obigrep -Z -s '^[acgt]+$' \
        wolf_noshort.fasta.gz \
        > wolf_acgt.fasta.gz

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_noshort.fasta.gz mime type: text/fasta  
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     



In [32]:
obicount wolf_acgt.fasta.gz | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_acgt.fasta.gz mime type: text/fasta     

| entities |      n |
| -------- | ------ |
| variants |    435 |
| reads    | 25,280 |
| symbols  | 43,328 |


### Running obiclean

#### Evaluating the ration threshold

In [35]:
obiclean --save-ratio wolf_ratio.csv \
         --save-graph wolf_graph \
         wolf_acgt.fasta.gz \
         > wolf_obiclean_1.fasta

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_acgt.fasta.gz mime type: text/fasta     

INFO[0000] Sequence dataset of 435 sequeences loaded    
INFO[0000] Dataset composed of 4 samples                
                                                                       ror graph]  44% |██████         | (18389952 it/s) [0s:0s][One error graph]  59% |████████       | (17964160 it/s) [0s:0s][One error graph] 100% |███████████████| (19531142 it/s)[Annotate sequence status]  50% |███████        | (786 it/s) [0s:0s][Annotate sequence status]  75% |███████████    | (1141 it/s) [0s:0s][Annotate sequence status] 100% |███████████████| (1467 it/s)[Save GML Graph files]  50% |███████        | (1060 it/s) [0s:0s][Save GML Graph files]  75% |███████████    | (1202 it/s) [0s:0s][Save GML Graph files] 100% |███████████████| (1212 it/s)[Save CSV stat ratio file]   8% |█              | (81360 it/s) [0s:0s][Save CSV s

In [38]:
obiclean --detect-chimera \
         -r 0.1 -H \
         wolf_acgt.fasta.gz \
         > wolf_obiclean_2.fasta 

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_acgt.fasta.gz mime type: text/fasta     

INFO[0000] Sequence dataset of 435 sequeences loaded    
INFO[0000] Dataset composed of 4 samples                
                                                                              ph]  44% |██████         | (11275210 it/s) [0s:0s][One error graph]  59% |████████       | (10893174 it/s) [0s:0s][One error graph] 100% |███████████████| (12325209 it/s)[Filter graph on abundance ratio]  50% |███████        | (54237 it/s) [0s:0s][Filter graph on abundance ratio]  75% |███████████    | (47337 it/s) [0s:0s][Filter graph on abundance ratio] 100% |███████████████| (44017 it/s)[Annotate sequence status]  50% |███████        | (18476 it/s) [0s:0s][Annotate sequence status]  75% |███████████    | (15161 it/s) [0s:0s][Annotate sequence status] 100% |███████████████| (3483 it/s)INFO[0000] On output use JSON headers     

In [39]:
obicount wolf_obiclean_2.fasta | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_obiclean_2.fasta mime type: text/fasta  

| entities |      n |
| -------- | ------ |
| variants |     30 |
| reads    | 22,608 |
| symbols  |  2,987 |


## Taxonomical assignment

using `obitag`

In [41]:
obitag -R ./vert01_ref_db.fasta.gz \
       --save-db ./vert01_ref_db_indexed.fasta \
       wolf_obiclean_2.fasta \
       > wolf_taxon.fasta

INFO[0000] Number of workers set 32                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_obiclean_2.fasta mime type: text/fasta  
INFO[0000] ./vert01_ref_db.fasta.gz mime type: text/fasta 
INFO[0000] Set as default taxonomy taxon                
/ Reading sequences (1/-, 5 it/s) [0s] 
INFO[0000] 3851 reference sequences conserved on 3851   
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     


In [45]:
obiannotate --number wolf_taxon.fasta \
| obiannotat e --set-identifier 'sprintf("MOTU_%03d", annotations.seq_number)' \
      > wolf_short_id.fasta

INFO[0000] Number of workers set 16                     
INFO[0000] Number of workers set 16                     
INFO[0000] Reading sequences from stdin in guessed      
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_taxon.fasta mime type: text/fasta       
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     

INFO[0000] - mime type: text/fasta                      
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     



In [48]:
obigrep -p 'max(annotations.obiclean_weight) >= 100' \
        wolf_short_id.fasta \
        > wolf_no_rare.fasta

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_short_id.fasta mime type: text/fasta    
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     



In [49]:
obiannotate -k count \
            -k merged_sample \
            -k obiclean_weight \
            -k obitag_bestmatch \
            -k obitag_bestid \
            -k obitag_rank \
            -k taxid \
            wolf_no_rare.fasta \
            > wolf_taxon_cleaned.fasta

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_no_rare.fasta mime type: text/fasta     
INFO[0000] On output use JSON headers                   
INFO[0000] Output is done on stdout                     
INFO[0000] Data is writen to stdout                     



In [50]:
obicsv -i -s --auto \
       wolf_taxon_cleaned.fasta \
       > wolf_taxon_cleaned.csv

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_taxon_cleaned.fasta mime type: text/fasta 




In [51]:
obimatrix --transpose \
          -k id \
          -k taxid \
          -k obitag_bestid \
          --map obiclean_weight \
          wolf_no_rare.fasta | csvlook

INFO[0000] Number of workers set 16                     
INFO[0000] Found 1 files to process                     
INFO[0000] wolf_no_rare.fasta mime type: text/fasta     

| taxon                                    | id       | obitag_bestid | 13a_F730603 | 15a_F730814 | 26a_F040644 | 29a_F260619 |
| ---------------------------------------- | -------- | ------------- | ----------- | ----------- | ----------- | ----------- |
| taxon:9611 [Canis]@genus                 | MOTU_066 |        1.000… |           9 |           4 |         328 |           1 |
| taxon:9992 [Marmota]@genus               | MOTU_006 |        0.990… |           0 |           0 |       8,744 |           0 |
| taxon:35500 [Pecora]@infraorder          | MOTU_014 |        0.950… |           0 |           0 |           0 |         152 |
| taxon:9860 [Cervus elaphus]@species      | MOTU_017 |        1.000… |       6,192 |           0 |           0 |           0 |
| taxon:55153 [Sciuridae]@family           | MOTU_020 |     